In [ ]:
pip install langchain langchain-openai langchain-chroma langchain-community


In [ ]:
pip install chromadb openai tiktoken python-dotenv

In [ ]:
import os
import dotenv
from openai import OpenAI

# Load API keys from .env file
dotenv.load_dotenv()

from langchain_openai import ChatOpenAI, OpenAIEmbeddings
from langchain_chroma import Chroma
from langchain_community.document_loaders import WebBaseLoader
from langchain_text_splitters import RecursiveCharacterTextSplitter
from langchain.chains.combine_documents import create_stuff_documents_chain
from langchain_core.prompts import ChatPromptTemplate
from langchain.chains import create_retrieval_chain

In [ ]:
os.environ["OPENAI_API_KEY"] = "your-api-key"

In [ ]:
loader = WebBaseLoader("https://lilianweng.github.io/posts/2023-06-23-agent/")
docs = loader.load()


In [ ]:
text_splitter = RecursiveCharacterTextSplitter(chunk_size=1000, chunk_overlap=100)
all_splits = text_splitter.split_documents(docs)

In [ ]:
vectorstore = Chroma.from_documents(
    documents=all_splits,
    embedding=OpenAIEmbeddings(),
    persist_directory="./chroma_db"   # saves database to disk
)

In [ ]:
retriever = vectorstore.as_retriever(search_type="similarity", search_kwargs={"k": 4})

In [ ]:
llm = ChatOpenAI(model="gpt-4o", temperature=0)

In [ ]:
system_template = """
Answer the user's question using the context below.
If the context does not provide the answer, reply with "I don't know."

<context>
{context}
</context>
"""
qa_prompt = ChatPromptTemplate.from_messages([
    ("system", system_template),
    ("human", "{input}")
])

In [ ]:
combine_docs_chain = create_stuff_documents_chain(llm, qa_prompt)

In [ ]:
retrieval_chain = create_retrieval_chain(retriever, combine_docs_chain)

In [ ]:

query = "What is the key idea of the paper?"
response = retrieval_chain.invoke({"input": query})

print("\nUser Query:", query)
print("Answer:", response["answer"])


User Query: What is the key idea of the paper?
Answer: The key idea of the paper is that any algorithm that generates a set of learning histories can be distilled into a neural network by performing behavioral cloning over actions. The history data is generated by a set of source policies, each trained for a specific task. During training, a random task is sampled and a subsequence of multi-episode history is used for training, making the learned policy task-agnostic.
